In [17]:
!pip install pandas


[notice] A new release of pip is available: 24.3.1 -> 25.1.1
[notice] To update, run: pip install --upgrade pip


In [18]:
import pandas as pd
from collections import defaultdict
import re

def parse_pow_logs(file_path):
    mined_blocks = defaultdict(list)
    created_txs = defaultdict(list)
    received_connectable = []
    received_orphan = []
    reorganizations = []

    with open(file_path, 'r') as f:
        for line in f:
            # extract simulation timestamp
            m_time = re.match(r"^(\d+\.\d+)", line)
            ts = float(m_time.group(1)) if m_time else None

            if "mined block" in line:
                m = re.search(
                    r"Node (\d+) mined block (\S+) at height (\d+) with (\d+) txs: \[(.*?)\]",
                    line
                )
                if m:
                    node, blk_hash, height, n_txs, txhash_list = m.groups()
                    txhashes = [tx.strip() for tx in txhash_list.split(",") if tx.strip()]
                    mined_blocks[int(node)].append({
                        "node": int(node),
                        "block_hash": blk_hash,
                        "height": int(height),
                        "txs": int(n_txs),
                        "txhash_list": txhashes,
                        "time_mined": ts
                    })

            if "added new tx" in line:
                m = re.search(r"Node (\d+) added new tx (\S+) with fee (\d+) sat", line)
                if m:
                    node, txhash, fee = m.groups()
                    created_txs[int(node)].append({
                        "node": int(node),
                        "txhash": txhash,
                        "fee": int(fee),
                        "time_created": ts
                    })

            if "received directly connectable block" in line:
                m = re.search(r"Node (\d+) received directly connectable block (\S+)", line)
                if m:
                    node, blk = m.groups()
                    received_connectable.append({
                        "node": int(node),
                        "block_hash": blk,
                        "time_received": ts
                    })

            if "received orphan block" in line:
                m = re.search(r"Node (\d+) received orphan block (\S+)", line)
                if m:
                    node, blk = m.groups()
                    received_orphan.append({
                        "node": int(node),
                        "block_hash": blk,
                        "time_orphaned": ts
                    })

            if "reorganized chain" in line:
                m = re.search(
                    r"Node (\d+) reorganized chain: old tip=(\S+) new tip=(\S+)",
                    line
                )
                if m:
                    node, old_tip, new_tip = m.groups()
                    reorganizations.append({
                        "node": int(node),
                        "old_tip": old_tip,
                        "new_tip": new_tip,
                        "time_reorg": ts
                    })

    mined_df = pd.DataFrame(
        [entry for blks in mined_blocks.values() for entry in blks]
    )
    tx_df = pd.DataFrame(
        [entry for txs in created_txs.values() for entry in txs]
    )
    recv_conn_df = pd.DataFrame(received_connectable)
    recv_orphan_df = pd.DataFrame(received_orphan)
    reorg_df = pd.DataFrame(reorganizations)

    return mined_df, tx_df, recv_conn_df, recv_orphan_df, reorg_df


In [19]:
log_path = "src/ledger_logs.txt"
mined_df, tx_df, recv_conn_df, recv_orphan_df, reorg_df = parse_pow_logs(log_path)

print("Parsed mined blocks:", len(mined_df))
print("Parsed created txs:", len(tx_df))
print("Parsed direct-receive events:", len(recv_conn_df))
print("Parsed orphan-receive events:", len(recv_orphan_df))
print("Parsed reorg events:", len(reorg_df))

Parsed mined blocks: 10081
Parsed created txs: 199374
Parsed direct-receive events: 19988048
Parsed orphan-receive events: 13856
Parsed reorg events: 0


In [20]:
display(mined_df)

node            block_hash  height  txs  \
0        63  -5065710507366980413       0    0   
1        63  -7339778485506744943      34    5   
2        63   5144720468893511142     272   61   
3        63   -834956516765753132     448   58   
4        63  -6372446745314298780     554   26   
5        63   4173873002499468144     626   21   
6        63  -1307516503514707205     769   40   
7        63  -2898967931508103879     900   49   
8        63   6682874073539974094     950   11   
9        63   1000219861704970852    1025   19   
10       63  -6716253592078432988    1161   37   
11       63  -4518043918854624271    1298   49   
12       63   4081281481349662014    1305    1   
13       63   1393785088506670967    1352    7   
14       63  -6149218439842492060    1355    0   
15       63    612272519593014054    1371    6   
16       63   7693177665527642524    1513   24   
17       63  -4579100158917749676    1521    2   
18       63   3265082061539200761    1585    8   
19       63    837020974567416872    1712   40   
20       63  -1664988910449739001    1749   16   
21       63  -4494602734907317250    1810   14   
22       63  -7259288605685101384    1863   10   
23       63  -5641935961327099517    1908   13   
24       63  -8558722061966320478    2036   27   
25       63    604348940950029041    2064    4   
26       63  -8200870073213946524    2067    0   
27       63  -1168080897070821636    2088    4   
28       63  -7887811649004571065    2161   22   
29       63   2665480944228441345    2166    3   
30       63   3001809361471795318    2332   38   
31       63  -5774159909946694641    2793  129   
32       63   7930574308584617780    2794    1   
33       63   3823221508130400442    2798    1   
34       63   -572675733178904639    2800    1   
35       63  -6219610670281937442    2863    6   
36       63  -4109271932252060515    2936   19   
37       63  -6046068174051988178    3043   26   
38       63   4115282381731763124    3128   18   
39       63  -5473153662973044076    3185   19   
40       63  -8223644819821686869    3207    6   
41       63   5484645050960652002    3226    8   
42       63  -2372097152467512358    3313   20   
43       63  -8764985638789470711    3319    0   
44       63   8736202839985456709    3322    0   
45       63  -8367353915841486391    3333    0   
46       63  -2113633736609799041    3346    7   
47       63   2643482748567547937    3424   20   
48       63   5883831361670499315    3427    1   
49       63  -3311333899919936912    3430    0   
50       63  -8848610345961084886    3482   10   
51       63  -2430588355888367088    3590   29   
52       63  -1858631689364191450    3650   12   
53       63  -8809131777985478413    3696   12   
54       63   2365725531530505831    3801   30   
55       63  -8824406707334187506    3858    9   
56       63   3156303496507234617    3861    2   
57       63  -4093688787217203808    3902    8   
58       63   6966658864142281051    4093   50   
59       63    654395949483081871    4231   32   
60       63  -8839029725489672509    4284   12   
61       63   7509866291640898883    4372   21   
62       63  -7187301871762053394    4504   21   
63       63  -4699446354214494993    4540    7   
64       63   8525555739788697378    4545    0   
65       63   5161657582615679423    5087  146   
66       63   6522069681524382755    5142   13   
67       63  -1112832329612119974    5345   54   
68       63   9139898192992628924    5352    4   
69       63   4440552471627559338    5630   78   
70       63   7418042978823629733    5764   32   
71       63  -2206116596698112071    5982   46   
72       63   3206405786327780804    6123   33   
73       63   9061134870973222210    6133    1   
74       63    -79021551629331652    6135    1   
75       63  -5990509395537990728    6179    6   
76       63  -8735418209017187788    6290   31   
77       63   5865804721622508776    6294    1   
78       63   6100342674910245889    6341   10   
79     

In [21]:
    events = []
    pat_gen = re.compile(r"Node (\d+): genesis block (\S+) added") # get the start of the chain
    pat_add = re.compile(r"Node (\d+): added block (\S+) under parent (\S+)") # get all blocks added
    with open(log_path, 'r') as f:
        for line in f:
            m = pat_gen.search(line)
            if m:
                node, blk = m.groups()
                events.append((int(node), blk, None))
                continue
            m = pat_add.search(line)
            if m:
                node, blk, parent = m.groups()
                events.append((int(node), blk, parent))
    
    # Build parent map per node
    parent_map = defaultdict(dict)
    for node, blk, parent in events:
        parent_map[node][blk] = parent # We know the parent of every block the node accepted
    
    # Function to build chain from tip to genesis
    def build_chain(pm, tip):
        #  takes a block at the end (the tip) and walks backward through parent links until it reaches the genesis.

        chain = []
        cur = tip
        while cur is not None:
            chain.append(cur)
            cur = pm.get(cur)
        return list(reversed(chain)) # reverse to return in correct order
    
    # Reconstruct best chain per node and pick global reference
    node_chains = {}
    for node, pm in parent_map.items():
        leaves = set(pm.keys()) - {p for p in pm.values() if p is not None}
        best = []
        for leaf in leaves: # For each leaf, builds a chain back to genesis.
            c = build_chain(pm, leaf)
            if len(c) > len(best): best = c
        node_chains[node] = best # Choose  the longest chain from among leafes
    
    # 3.5 Choose the single longest chain
    ref_chain = max(node_chains.values(), key=len) # Pick the single longest chain overall using
    print(f"Derived reference chain of length {len(ref_chain)}")

Derived reference chain of length 7833


In [22]:
main_chain_df = (
    mined_df.drop_duplicates('block_hash')
            .set_index('block_hash')
            .loc[ref_chain]
            .reset_index()
)

pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)
main_chain_df_sorted = main_chain_df.sort_values(by=['node', 'height'])
display(main_chain_df_sorted[['node','block_hash','height','txs','txhash_list']])



node            block_hash  height  txs  \
63       0  -2229827867398106359      63   11   
227      0   7364876751649294310     227    1   
241      0  -7691701143488274330     241    2   
243      0  -2491771375731302693     243    0   
377      0   9023421358493475090     377   40   
504      0   2438402138095685243     504   25   
607      0   7827693579707588355     607    9   
697      0  -7933873410110821866     697   25   
770      0    402233239664213570     770   25   
791      0   -512136454530710195     791   10   
864      0  -5617074692113028427     864   19   
897      0   8735749040444253525     897    3   
918      0  -1093875159668659330     918    9   
922      0  -6608229856215635825     922    1   
1052     0  -5961065246180344618    1052   33   
1066     0   7701465382248616994    1066    8   
1274     0   7045753848672694030    1274   61   
1308     0   4928284343282558363    1308   10   
1378     0   3431033747228243019    1378   25   
1407     0   5522709568761030603    1407    9   
1532     0  -4226613958048832030    1532   33   
1813     0   6087279530632814005    1813   68   
2028     0    763377904902854135    2028   57   
2061     0   5701133310421931678    2061    8   
2220     0  -1196923797194242445    2220   35   
2289     0   8383283766923663314    2289   15   
2306     0   -747302190193706524    2306    8   
2425     0   5034677820117058634    2425    9   
2515     0  -6269454624601610119    2515   25   
2653     0   5464895445119119135    2653   30   
2801     0  -6753252464409921170    2801   39   
2864     0   2752881025347010034    2864   15   
2865     0   7429996394984539939    2865    0   
3170     0   5711628259583926867    3170   84   
3210     0   8148043937515990241    3210   11   
3334     0   8741777029044319804    3334   29   
3471     0  -4021325178678470149    3471   14   
3511     0   6193441689640911999    3511    7   
3790     0  -3276657150876862810    3790   83   
3794     0    516792900972428990    3794    1   
4043     0   -831616084574037875    4043   53   
4070     0  -7480040151217688367    4070   12   
4087     0   8113671735661486963    4087    4   
4341     0   6700671170506094045    4341   71   
4416     0   2106113953295273015    4416   25   
4470     0   -571632471043093427    4470   18   
4634     0  -1179711700623596190    4634   45   
4813     0  -6189486610045040567    4813    6   
4951     0   6296569821177057933    4951   39   
4973     0  -1268421279474375058    4973   11   
4978     0  -3766188316638305569    4978    2   
4985     0  -5625686600909250727    4985    0   
5077     0   6189538622255428125    5077   19   
5455     0   5748095611701297521    5455   89   
5588     0   2920884341972772276    5588   14   
5686     0  -6172496315140153045    5686   21   
5841     0   1013383919447009963    5841    7   
6015     0   1707004461150766694    6015   35   
6215     0  -8933986234789221363    6215    7   
6571     0  -3271963690709698367    6571   97   
6622     0  -7587957668430882262    6622   14   
6681     0  -6694453026401267206    6681   19   
6684     0    221703169949932597    6684    0   
6851     0   7441369531871646120    6851   29   
6944     0  -6733762629451299422    6944   27   
7041     0   8929979710096131656    7041   30   
7150     0   -134783861624051524    7150   25   
7229     0   7460830705544213113    7229   24   
7261     0   4508649500244904300    7261    7   
7325     0  -1208366132110079824    7325   13   
7494     0  -3415428362374806465    7494   54   
7511     0   7327576365137757646    7511    4   
7540     0   4571135547773073831    7540    8   
7551     0  -2915688025475550472    7551    2   
7556     0   7806651198683464476    7556    0   
7601     0   6205598590249339121    7601   11   
7610     0  -6642463761934380418    7610    1   
7786     0   7764891928075438191    7786   57   
47       1   5130001426566481410      47   13   
212      1  -8614631442359761637     212   23   
283      1  -6629214677047217908     

In [23]:
# Per-node breakdown of tx slots and unique
slots_per_node  = main_chain_df.groupby('node')['txs'].sum().rename('tx_slots')
unique_per_node = main_chain_df.groupby('node')['txhash_list'] \
                        .apply(lambda lists: {tx for lst in lists for tx in lst}) \
                        .apply(len) \
                        .rename('unique_tx_count')

agg_df = pd.concat([slots_per_node, unique_per_node], axis=1)
print(agg_df)

      tx_slots  unique_tx_count
node                           
0         1797             1797
1         1520             1520
2         1639             1639
3         1578             1578
4         1523             1523
5         1625             1625
6         1450             1450
7         1523             1523
8         1476             1476
9         1489             1489
10        1616             1616
11        1513             1513
12        1344             1344
13        1563             1563
14        1342             1342
15        1599             1599
16        1388             1388
17        1700             1700
18        1644             1644
19        1624             1624
20        1259             1259
21        1642             1642
22        1420             1420
23        1700             1700
24        1529             1529
25        1738             1738
26        1673             1673
27        1824             1824
28        1697             1697
29      

In [24]:
# Metrics on Main Chain

#Compute throughput, orphan rate, transaction confirmation, etc., focusing only on the main chain.

print(f"Main chain length: {len(ref_chain)} blocks")
total_txs_main = main_chain_df['txs'].sum()
print(f"Total txs in main chain: {total_txs_main}")
print(f"Average txs per block (main): {total_txs_main/len(ref_chain):.2f}")


Main chain length: 7833 blocks
Total txs in main chain: 154495
Average txs per block (main): 19.72


In [25]:
total_created = tx_df['txhash'].nunique()
print(f"Total TXs created: {total_created}")

Total TXs created: 199371


In [26]:
# TXs in final chain
final_txhashes = {tx for lst in main_chain_df['txhash_list'] for tx in lst}
total_final = len(final_txhashes)
print(f"TXs in final chain: {total_final}")
chain_blocks = main_chain_df

TXs in final chain: 154494


In [27]:
# Transactions with ≥6 confirmations
# Build first-index map from main chain data
chain_blocks = main_chain_df.set_index('block_hash').loc[ref_chain]
tx_first_idx = {}
for idx, (blk_hash, row) in enumerate(chain_blocks.iterrows()):
    for tx in row['txhash_list']:
        tx_first_idx.setdefault(tx, idx)
# Compute depths and count those ≥6 confirmations
depths = [len(ref_chain) - tx_first_idx.get(tx, 0) for tx in final_txhashes]
total_ge6 = sum(1 for d in depths if d >= 6)
print(f"TXs ≥6 confirmations: {total_ge6}")

TXs ≥6 confirmations: 154344
